In [1]:
import matplotlib.pyplot as plt

import geopandas as gpd


import pandas as pd
from pandas.io.json import json_normalize
import math

import numpy as np


import folium

import json
import geojson
from shapely.geometry import Point

import requests

In [2]:
'''
ALTIJD:
Output Fields = *
Output Spatial Reference = 4326
Format = GeoJSON

Als je meer dan 2000 datapoints moet laden:
resultType = standard
'''
#URL'S:

#Outlines of camps 14, 15, 16
camp_outlines = 'https://services5.arcgis.com/QYf5PkPqzJKVzrmF/arcgis/rest/services/Rohingya_Refugee_Camps_Sites_Outline_May_18/FeatureServer/0/query?where=New_Camp_N+%3D+%27Camp+14%27+OR+New_Camp_N++%3D++%27Camp+15%27+OR+New_Camp_N++%3D+%27Camp+16%27&objectIds=&time=&geometry=&geometryType=esriGeometryEnvelope&inSR=&spatialRel=esriSpatialRelIntersects&resultType=none&distance=0.0&units=esriSRUnit_Meter&returnGeodetic=false&outFields=*&returnGeometry=true&returnCentroid=false&multipatchOption=xyFootprint&maxAllowableOffset=&geometryPrecision=&outSR=4326&datumTransformation=&applyVCSProjection=false&returnIdsOnly=false&returnUniqueIdsOnly=false&returnCountOnly=false&returnExtentOnly=false&returnDistinctValues=false&orderByFields=&groupByFieldsForStatistics=&outStatistics=&having=&resultOffset=&resultRecordCount=&returnZ=false&returnM=false&returnExceededLimitFeatures=true&quantizationParameters=&sqlFormat=none&f=pgeojson&token='
#Subsections of camps 14, 15, 16
ssc_all = 'https://services5.arcgis.com/QYf5PkPqzJKVzrmF/arcgis/rest/services/Updated_Majhee_Block_May_18/FeatureServer/0/query?where=SiteName+%3D+%27Camp+14%27+OR+SiteName+%3D++%27Camp+15%27+OR+SiteName+%3D+%27Camp+16%27&objectIds=&time=&geometry=&geometryType=esriGeometryEnvelope&inSR=&spatialRel=esriSpatialRelIntersects&resultType=none&distance=0.0&units=esriSRUnit_Meter&returnGeodetic=false&outFields=*&returnGeometry=true&returnCentroid=false&multipatchOption=xyFootprint&maxAllowableOffset=&geometryPrecision=&outSR=4326&datumTransformation=&applyVCSProjection=false&returnIdsOnly=false&returnUniqueIdsOnly=false&returnCountOnly=false&returnExtentOnly=false&returnDistinctValues=false&orderByFields=&groupByFieldsForStatistics=&outStatistics=&having=&resultOffset=&resultRecordCount=&returnZ=false&returnM=false&returnExceededLimitFeatures=true&quantizationParameters=&sqlFormat=none&f=pgeojson&token='
#WASH infrastrucutre of camps 14, 15, 16
wash = 'https://services5.arcgis.com/QYf5PkPqzJKVzrmF/arcgis/rest/services/Updated_WASH_infrastructure_Round_7/FeatureServer/0/query?where=Camp_name+%3D+%27Camp+14%27+OR+Camp_name+%3D++%27Camp+15%27+OR+Camp_name%3D+%27Camp+16%27&objectIds=&time=&geometry=&geometryType=esriGeometryEnvelope&inSR=&spatialRel=esriSpatialRelIntersects&resultType=standard&distance=0.0&units=esriSRUnit_Meter&returnGeodetic=false&outFields=*&returnGeometry=true&multipatchOption=xyFootprint&maxAllowableOffset=&geometryPrecision=&outSR=4326&datumTransformation=&applyVCSProjection=false&returnIdsOnly=false&returnUniqueIdsOnly=false&returnCountOnly=false&returnExtentOnly=false&returnDistinctValues=false&orderByFields=&groupByFieldsForStatistics=&outStatistics=&having=&resultOffset=&resultRecordCount=&returnZ=false&returnM=false&returnExceededLimitFeatures=true&quantizationParameters=&sqlFormat=none&f=pgeojson&token='

#Subsections Camp 14
ssc14 = 'https://services5.arcgis.com/QYf5PkPqzJKVzrmF/arcgis/rest/services/Updated_Majhee_Block_May_18/FeatureServer/0/query?where=SiteName+%3D+%27Camp+14%27&objectIds=&time=&geometry=&geometryType=esriGeometryEnvelope&inSR=&spatialRel=esriSpatialRelIntersects&resultType=standard&distance=0.0&units=esriSRUnit_Meter&returnGeodetic=false&outFields=*&returnGeometry=true&returnCentroid=false&multipatchOption=xyFootprint&maxAllowableOffset=&geometryPrecision=&outSR=4326&datumTransformation=&applyVCSProjection=false&returnIdsOnly=false&returnUniqueIdsOnly=false&returnCountOnly=false&returnExtentOnly=false&returnDistinctValues=false&orderByFields=&groupByFieldsForStatistics=&outStatistics=&having=&resultOffset=&resultRecordCount=&returnZ=false&returnM=false&returnExceededLimitFeatures=true&quantizationParameters=&sqlFormat=none&f=pgeojson&token='
#Subsections Camp 15
ssc15 = 'https://services5.arcgis.com/QYf5PkPqzJKVzrmF/arcgis/rest/services/Updated_Majhee_Block_May_18/FeatureServer/0/query?where=SiteName+%3D+%27Camp+15%27&objectIds=&time=&geometry=&geometryType=esriGeometryEnvelope&inSR=&spatialRel=esriSpatialRelIntersects&resultType=standard&distance=0.0&units=esriSRUnit_Meter&returnGeodetic=false&outFields=*&returnGeometry=true&returnCentroid=false&multipatchOption=xyFootprint&maxAllowableOffset=&geometryPrecision=&outSR=4326&datumTransformation=&applyVCSProjection=false&returnIdsOnly=false&returnUniqueIdsOnly=false&returnCountOnly=false&returnExtentOnly=false&returnDistinctValues=false&orderByFields=&groupByFieldsForStatistics=&outStatistics=&having=&resultOffset=&resultRecordCount=&returnZ=false&returnM=false&returnExceededLimitFeatures=true&quantizationParameters=&sqlFormat=none&f=pgeojson&token='
#WASH Camp 15
wash15 = 'https://services5.arcgis.com/QYf5PkPqzJKVzrmF/arcgis/rest/services/Updated_WASH_infrastructure_Round_7/FeatureServer/0/query?where=Camp_name+%3D+%27Camp+15%27&objectIds=&time=&geometry=&geometryType=esriGeometryEnvelope&inSR=&spatialRel=esriSpatialRelIntersects&resultType=standard&distance=0.0&units=esriSRUnit_Meter&returnGeodetic=false&outFields=*&returnGeometry=true&multipatchOption=xyFootprint&maxAllowableOffset=&geometryPrecision=&outSR=4326&datumTransformation=&applyVCSProjection=false&returnIdsOnly=false&returnUniqueIdsOnly=false&returnCountOnly=false&returnExtentOnly=false&returnDistinctValues=false&orderByFields=&groupByFieldsForStatistics=&outStatistics=&having=&resultOffset=&resultRecordCount=&returnZ=false&returnM=false&returnExceededLimitFeatures=true&quantizationParameters=&sqlFormat=none&f=pgeojson&token='

#Subsections Camp 16
ssc16 = 'https://services5.arcgis.com/QYf5PkPqzJKVzrmF/arcgis/rest/services/Updated_Majhee_Block_May_18/FeatureServer/0/query?where=SiteName+%3D+%27Camp+16%27&objectIds=&time=&geometry=&geometryType=esriGeometryEnvelope&inSR=&spatialRel=esriSpatialRelIntersects&resultType=none&distance=0.0&units=esriSRUnit_Meter&returnGeodetic=false&outFields=*&returnGeometry=true&returnCentroid=false&multipatchOption=xyFootprint&maxAllowableOffset=&geometryPrecision=&outSR=4326&datumTransformation=&applyVCSProjection=false&returnIdsOnly=false&returnUniqueIdsOnly=false&returnCountOnly=false&returnExtentOnly=false&returnDistinctValues=false&orderByFields=&groupByFieldsForStatistics=&outStatistics=&having=&resultOffset=&resultRecordCount=&returnZ=false&returnM=false&returnExceededLimitFeatures=true&quantizationParameters=&sqlFormat=none&f=pgeojson&token='


In [3]:
outlines = requests.get(camp_outlines)
outlines_results = outlines.json()



outlines_df = json_normalize(outlines_results['features'])

outlines_df = outlines_df.rename(columns={'properties.New_Camp_N': 'properties.SiteName'})

#print(outlines_df)

m = folium.Map(
    location=[21.1584, 92.1384],
    tiles='Mapbox Bright',
    zoom_start=13
)

folium.GeoJson(
    outlines_results,
    name='geojson'
).add_to(m)

ssc = requests.get(ssc_all)
ssc_results = ssc.json()

ssc_df = json_normalize(ssc_results['features'])

ssc_df['avg.household'] = ssc_df['properties.Total_Pop']/ssc_df['properties.Total_HH']

#print(ssc_df.head())

m.choropleth(
    geo_data=ssc_results,
    data=ssc_df,
    columns=['id', 'avg.household'],
    key_on='feature.id',
    fill_color='BuPu',
    legend_name='Average no. of People per Household'
)


folium.LayerControl().add_to(m)

m.save('ppperhousehold.html')

m

In [10]:
style_function = lambda x: {'fillColor': 'none'}

m1 = folium.Map(
    location=[21.1584, 92.1384],
    tiles='Mapbox Bright',
    zoom_start=13
)

folium.GeoJson(
    outlines_results,
    name='Camp Outlines',
    style_function=style_function 
).add_to(m1)

folium.GeoJson(
    ssc_results,
    name='Subsections',
    style_function=style_function    
).add_to(m1)

wash_infra = requests.get(wash)
wash_results = wash_infra.json()

wash_df = json_normalize(wash_results['features'])

#print(wash_df.head())

def wash_colors(type):
    colors = {'Unimproved water source' : '#ffffff',
     'Tapstand' : '#ffffff', 
     'Water Tank': '#ffffff', 
     'Pit or dump point': '#ffffff', 
     'Wash Room(s)': '#ffffff', 
     'Hand Pump - Tubewell': '#ffffff', 
     'Decommissioned Latrine': '#ffffff', 
     'Latrine(s)': '#00ff00'}
    return colors[type]

def plot_wash(wash_df, wash_type, folium_map):
    #Plot a certain type of WASH infra (indicated by the wash_type input)
    
    for index, row in wash_df.iterrows():
        if row['properties.Type'] == wash_type:
            folium.Circle(
                location=[row['properties.Latitude'], row['properties.Longitude']],
                radius=10,
                popup=wash_type,
                color='#3186cc',
                fill=True,
                fill_color='#3186cc',
                fill_opacity=0.5,
                line_opacity=0.7
            ).add_to(folium_map)

plot_wash(wash_df, 'Latrine(s)', m1)

m1

In [21]:
#m1.save('latrines_10m_radius.html')
m2 = folium.Map(
    location=[21.1584, 92.1384],
    tiles='Mapbox Bright',
    zoom_start=13
)

folium.GeoJson(
    outlines_results,
    name='Camp Outlines',
    style_function=style_function 
).add_to(m2)

folium.GeoJson(
    ssc_results,
    name='Subsections',
    style_function=style_function    
).add_to(m2)

from folium.plugins import HeatMap

latrines_df = wash_df.loc[wash_df['properties.Type'] == 'Latrine(s)'] 
geodata_latrines=[[row['properties.Latitude'],row['properties.Longitude']] for index, row in latrines_df.iterrows()]

HeatMap(geodata_latrines).add_to(m2)

m2

m2.save('latrines_heatmap.html')